# 1. Importing and Visualization of CIFAR-10 Dataset

In [ ]:
import numpy as np

# function to import CIFAR-10 data set
def unpickle(file):
    import pickle
    with open(file, 'rb') as fo:
        dict = pickle.load(fo, encoding='bytes')
    return dict
data_batch_1 = unpickle("./data/data_batch_1")
data_batch_2 = unpickle("./data/data_batch_2")
data_batch_3 = unpickle("./data/data_batch_3")
data_batch_4 = unpickle("./data/data_batch_4")
data_batch_5 = unpickle("./data/data_batch_5")
test_batch = unpickle("./data/test_batch")

What is the data structure of e.g. data_batch_1 ?

In [ ]:
type(data_batch_1)

What are the keys of e.g. data_batch_1 ?

In [ ]:
data_batch_1.keys()

What is the data structure of data_batch_1[b'data'] ?

In [ ]:
type(data_batch_1[b'data'])

What is the data structure of data_batch_1[b'labels'] ?

In [ ]:
type(data_batch_1[b'labels'])

What is the shape of data_batch_1[b'data'] ?

In [ ]:
data_batch_1[b'data'].shape

What is the size of data_batch_1[b'labels'] ?


In [ ]:
len(data_batch_1[b'labels'])

What are the first 10 elements of data_batch_1[b'labels'] ?

In [ ]:
data_batch_1[b'labels'][:10]

What is the data type of data_batch_1[b'data'] ?

In [ ]:
data_batch_1[b'data'].dtype

Let us concatenate the batch training data

In [ ]:
X_train=np.concatenate([data_batch_1[b'data'], 
                         data_batch_2[b'data'], 
                         data_batch_3[b'data'], 
                         data_batch_4[b'data'], 
                         data_batch_5[b'data']], 
                         axis = 0)

Let us concatenate the training labels

In [ ]:
y_train=np.concatenate([data_batch_1[b'labels'] , 
                data_batch_2[b'labels'],
                data_batch_3[b'labels'],
                data_batch_4[b'labels'],
                data_batch_5[b'labels']], 
                axis = 0)

Let us define the test data as X_test

In [ ]:
X_test = test_batch[b'data']
X_test.shape

Let us cast the test labels as ndarray

In [ ]:
y_test=np.array(test_batch[b'labels']) 
y_test.shape

What is the shape of X_train ?

In [ ]:
X_train.shape

What is the shape of Y_train ?

In [ ]:
y_train.shape

Let us visualize an image. 

In [ ]:
%matplotlib inline
import matplotlib.pyplot as plt

plt.imshow(X_train[20].reshape((3,32,32)).transpose((1,2,0)).astype('uint8'))
plt.show()


- By means of `reshape` we can convert an array from one shape to another without 
copying any data. To do this, we pass a tuple indicating the new shape to the `reshape` array instance method. 

- By default, `NumPy` arrays are created in _row major_ order. Spatially this means, that if we have a two-dimensional array of data, the items in each row of the array are stored in adjacent memory locations. In the case of a three-dimensional array of data, the items along `axis=2` are stored in adjacent order. Since the first 32 entries of the array `X_train[0]` are the red channel values of the first row of the image, etc., we need to pass the tuple $(3,32,32)$ to `reshape`. In conclusion, when __reshaping__ the array, higher order dimensions are traversed _first_ (e.g. axis $ 2 $ before advancing on axis $ 1 $.) 

- `plt.imshow` needs for each inner list the values representing a pixel. Here, with 
an RGB image, there are 3 values. We thus need to transpose the array : the RGB values need to be located along `axis=2`. 

- Using ndarray's `astype` method, we can cast an array from one `dtype` to another. `uint8` represents unsigned 8-bit integer types. Why 8 bits? Most displays can only render 8 bits per channel worth of color gradation. Why can they only render 8 bits/channel? Because that is about all the human eye can see.

We visualize some examples from the dataset.
We show a few examples of training images from each class.

In [ ]:
%matplotlib inline
classes = ['plane', 'car', 'bird', 'cat', 'deer', 'dog', 'frog', 'horse', 'ship', 'truck']
num_classes = len(classes)
samples_per_class = 7



for y, cls in enumerate(classes):
    idxs = np.flatnonzero(y_train == y)
    idxs = np.random.choice(idxs, samples_per_class, replace=False)
    for i, idx in enumerate(idxs):
        plt_idx = i * num_classes + y + 1
        plt.subplot(samples_per_class, num_classes, plt_idx)
        plt.imshow(X_train[idx].reshape((3,32,32)).transpose((1,2,0)).astype('uint8'))
        plt.axis('off')
        if i == 0:
            plt.title(cls)
plt.show()

- When iterating over a sequence we often want to keep track of the index of the 
current item. Python's built-in function `enumerate` returns a sequence of $i$, value 
tuples.

- `np.flatnonzero` returns indices that are non-zero in the (flattened version of) `y_train == y`, that is, it returns the indices for the elements that are `True`.

- `np.random.choice(..., replace=False)` generates a random sample from a given 1-D array without replacement.


- The `subplot()` command specifies `numrows`, `numcols`, `fignum` where `fignum` ranges from $ 1 $ to `numrows*numcols`.

# 2. K-Nearest-Neighbour Classifier

 We subsample the data for more efficient code execution in this exercise.

In [ ]:
num_training = 5000
mask = range(num_training)
X_train = X_train[mask]
y_train = y_train[mask]

num_test = 500
mask = range(num_test)
X_test = X_test[mask]
y_test = y_test[mask]

We define Class KNearestNeighbor.

In [ ]:
class KNearestNeighbor():
  """ a kNN classifier with L2 distance """

  def __init__(self):
    pass

  def train(self, X, y):
    """
    Train the classifier. For k-nearest neighbors this is just 
    memorizing the training data.

    Inputs:
    - X: A numpy array of shape (num_train, D) containing the training data
      consisting of num_train samples each of dimension D.
    - y: A numpy array of shape (N,) containing the training labels, where
         y[i] is the label for X[i].
    """
    self.X_train = X.astype('float')
    self.y_train = y
    
  def predict(self, X, k=1, num_loops=0):
    """
    Predict labels for test data using this classifier.

    Inputs:
    - X: A numpy array of shape (num_test, D) containing test data consisting
         of num_test samples each of dimension D.
    - k: The number of nearest neighbors that vote for the predicted labels.
    - num_loops: Determines which implementation to use to compute distances
      between training points and testing points.

    Returns:
    - y: A numpy array of shape (num_test,) containing predicted labels for the
      test data, where y[i] is the predicted label for the test point X[i].  
    """
    if num_loops == 0:
      dists = self.compute_distances_no_loops(X)
    elif num_loops == 1:
      dists = self.compute_distances_one_loop(X)
    elif num_loops == 2:
      dists = self.compute_distances_two_loops(X)
    else:
      raise ValueError('Invalid value %d for num_loops' % num_loops)

    return self.predict_labels(dists, k=k)

  def compute_distances_two_loops(self, X):
    """
    Compute the distance between each test point in X and each 
    training point in self.X_train using a nested loop over both 
    the training data and the test data.

    Inputs:
    - X: A numpy array of shape (num_test, D) containing test data.

    Returns:
    - dists: A numpy array of shape (num_test, num_train) where 
      dists[i, j] is the Euclidean distance between the ith test 
      point and the jth training point.
    """
    num_test = X.shape[0]
    num_train = self.X_train.shape[0]
    dists = np.zeros((num_test, num_train))
    X = X.astype('float')
    for i in range(num_test):
      for j in range(num_train):
          dists[i, j] = np.sqrt(np.sum(np.square(self.X_train[j,:] - X[i,:])))
        
    return dists

  def compute_distances_one_loop(self, X):
    """
    Compute the distance between each test point in X and each training point
    in self.X_train using a single loop over the test data.

    Input / Output: Same as compute_distances_two_loops
    """
    num_test = X.shape[0]
    num_train = self.X_train.shape[0]
    dists = np.zeros((num_test, num_train))
    X = X.astype('float')
    for i in range(num_test):
      dists[i, :] = np.sqrt(np.sum(np.square(self.X_train - X[i,:]), axis = 1))
      
     
    return dists

  def compute_distances_no_loops(self, X):
    """
    Compute the distance between each test point in X and each training point
    in self.X_train using no explicit loops.

    Input / Output: Same as compute_distances_two_loops
    """
    num_test = X.shape[0]
    num_train = self.X_train.shape[0]
    dists = np.zeros((num_test, num_train)) 
    X=X.astype('float')
    
    # Most "elegant" solution leads however to memory issues
    # dists = np.sqrt(np.square((self.X_train[:, np.newaxis, :] - X)).sum(axis=2)).T
    # split (p-q)^2 to p^2 + q^2 - 2pq
    dists = np.sqrt((X**2).sum(axis=1)[:, np.newaxis] + (self.X_train**2).sum(axis=1) - 2 * X.dot(self.X_train.T))
                     
    
    
    return dists

  def predict_labels(self, dists, k=1):
    """
    Given a matrix of distances between test points and training points,
    predict a label for each test point.

    Inputs:
    - dists: A numpy array of shape (num_test, num_train) where dists[i, j]
      gives the distance betwen the ith test point and the jth training point.

    Returns:
    - y: A numpy array of shape (num_test,) containing predicted labels for the
      test data, where y[i] is the predicted label for the test point X[i].  
    """
    num_test = dists.shape[0]
    y_pred = np.zeros(num_test, dtype='float64')
    for i in range(num_test):
        # A list of length k storing the labels of the k nearest neighbors to
        # the ith test point.
        closest_y = []
        # get the k indices with smallest distances
        min_indices = np.argsort(dists[i,:])[:k] 
        closest_y = np.bincount(self.y_train[min_indices])
        # predict the label of the nearest example
        y_pred[i] = np.argmax(closest_y)  

    return y_pred

- Methods within a class are defined in much the same way as functions, that is, using `def`. Every defined class has a _special method_ called `__init__()`  `Python` runs automatically whenever we create a new _instance_ based on the `NearestNeighbor` 
class. The `self` parameter is required in the method definition, and it must come first 
before the other parameters. It must be included in the definition because when `Python` 
calls this `__init__` method later (to create an instance of `NearestNeighbor`), 
the method call will automatically pass the `self` argument. Every method call associated with a class automatically passes `self`, which is a reference to the instance itself; 
it gives the individual instance access to the attributes and methods in the class. In summary, when you invoke a class method on an object instance, `Python` 
arranges for the first argument to be the invoking object instance, which is always 
assigned to each method's `self` argument.

- The two variables `self.X_train` and `self.y_train` each have the prefix `self`. Any variable prefixed with `self` is available to every method in the class, and we will also be able to access these variables through any instance created from the class. `self.X_train = X` takes the value stored in the parameter `X` and stores it in the variable `self.X_train`, which is then attached to the instance being created. The same process happens with `self.y_train = y`. 

- Variables that are accessible through instances like this are called _attributes_.
`np.zeros` produces an array of $ 0 $'s, here the size is `num_test`.

- `np.sum` returns the sum of all elements in the array or along an axis. Zero-length 
arrays have sum $ $ 0.

- `np.argmin` returns the index of minimum element.

- When Python reads the line `nn = NearestNeighbor()`, it calls the `__init__()` method in `NearestNeighbor()`. The `__init__()` method creates an instance representing this particular nearest neighbor classifier. The `__init__()` method has no explicit return statement, but Python automatically returns an instance representing this nearest neighbor classifier. We store that instance in the variable `nn`. The naming convention is helpful here: we can usually assume that a capitalized name like `NearestNeighbor()` refers to a class, and a lowercase name like `nn` refers to a single instance created from a class.


- `np.argsort` returns the indices that would sort an array.

- `np.bincount(x)` counts the number of occurrences of each value in an array of non-negative integers. The number of bins (of size 1) is one larger than the largest value in $ x $.

- Instead of a loop that contains a _broadcasting_ process with a 2D array 

`for i in range(num_test):
      dists[i, :] = np.sqrt(np.sum(np.square(self.X_train - X[i,:]), axis = 1))`

we can speed up this process by broadcasting with a 3D array 

`dists = np.sqrt(np.square((self.X_train[:, np.newaxis, :] - X)).sum(axis=2))`

- The _Broadcasting rule_ states: two arrays are compatible for broadcasting if for each 
_trailing dimension_ (that is, starting from the end of an array), the axis lengths match or if either of the lengths is 1. In the case of `self._train[:, np.newaxis, :]`, the trailing dimension is $2$ and the axis length $D$. The trailing dimension of `X` is 1 and has axis length $D$. Thus, they match. Broadcasting is then performed over the missing and / or length $ 1 $ dimensions. If we need to add a new axis with length $ 1 $ specifically for broadcasting purposes, `NumPy` arrays offer a special syntax for inserting new axes by indexing. We use the special `np.newaxis` attribute along with full slices to insert the new axis. We may imagine that `num_test` copies of `self.X_train` are tiled up along `axis=1` of `self.X_train[:, np.newaxis, :]`. On the other hand, `num_train` copies of `X` are tiled up on top of each other. First, the subtraction is performed along `axis=2`. Then, it is performed along `axis=1`, and finally over `axis=0`. The resulting shape of the subtraction then is (`num_train`, `num_test`, D). Since this runs into memory issues, we need to rewrite it as follows:

`dists = np.sqrt((X**2).sum(axis=1)[:, np.newaxis] + (self.X_train**2).sum(axis=1) - 2 * X.dot(self.X_train.T))`

which yields an array with shape (`num_test`, `num_train`, D)

- It is important to cast the data files as `float`.

Create an instance nn from the class KNearestNeighbor

In [ ]:
classifier = KNearestNeighbor()

We call the method `train` of the `KNearestNeighbor` class.

In [ ]:
classifier.train(X_train, y_train)

We test our implementation with two_loops

In [ ]:
dists = classifier.compute_distances_two_loops(X_test)
dists.shape  

We can visualize the distance matrix: each row is a single test example and its distances to training examples

In [ ]:
plt.imshow(dists, interpolation='none')
plt.show()

Let us now predict labels and run the code below: We use $k = 1$ (which is Nearest Neighbor).

In [ ]:
y_test_pred = classifier.predict_labels(dists, k=1)

We compute and print the fraction of correctly predicted examples.

In [ ]:
num_correct = np.sum(y_test_pred == y_test)
accuracy = float(num_correct) / num_test
print('Got %d / %d correct => accuracy: %f' % (num_correct, num_test, accuracy))


 Let us now predict labels and run the code below: We use k = 10

In [ ]:
y_test_pred = classifier.predict_labels(dists, k=10)

We compute and print the fraction of correctly predicted examples.

In [ ]:
num_correct = np.sum(y_test_pred == y_test)
accuracy = float(num_correct) / len(y_test_pred)
print('Got %d / %d correct => accuracy: %f' % (num_correct, num_test, accuracy))

## Confusion Matrix

In [ ]:
# utility function for plotting confusion matrix
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.metrics import confusion_matrix

def plot_confmat(y_true, y_pred):
    """
    Plot the confusion matrix and save to user_files dir
    """
    conf_matrix = confusion_matrix(y_true, y_pred)
    fig = plt.figure(figsize=(9,9))
    ax = fig.add_subplot(111)
    sns.heatmap(conf_matrix,
                annot=True,
                fmt='.0f')
    plt.title('Confusion matrix')
    ax.set_xticklabels( classes)
    ax.set_yticklabels( classes)
    plt.ylabel('True')
    plt.xlabel('Predicted')
    
plot_confmat(y_test, y_test_pred)    

## Algebra and Performance of Distance Matrix Computation


To ensure that our vectorized implementation is correct, we make sure that it
agrees with the naive implementation. There are many ways to decide whether
two matrices are similar; one of the simplest is the Frobenius norm. In case
you haven't seen it before, the Frobenius norm of two matrices is the square
root of the squared sum of differences of all elements; in other words, reshape
the matrices into vectors and compute the Euclidean distance between them.

In [ ]:
dists_two  = classifier.compute_distances_two_loops(X_test)
dists_one  = classifier.compute_distances_one_loop(X_test)
dists_zero = classifier.compute_distances_no_loops(X_test)


difference_two_2_one = np.linalg.norm(dists_two - dists_one, ord='fro')
print('Difference was: %f' % (difference_two_2_one, ))
if difference_two_2_one < 0.001:
  print('Good! The distance matrices are the same')
else:
  print('Uh-oh! The distance matrices are different')

difference_one_2_zero = np.linalg.norm(dists_one - dists_zero, ord='fro')
print('Difference was: %f' % (difference_one_2_zero, ))
if difference_one_2_zero < 0.001:
  print('Good! The distance matrices are the same')
else:
  print('Uh-oh! The distance matrices are different')

Let's compare how fast the implementations are

In [ ]:
def time_function(f, *args):
  """
  Call a function f with args and return the time (in seconds) that it took to execute.
  """
  import time
  tic = time.time()
  f(*args)
  toc = time.time()
  return toc - tic

two_loop_time = time_function(classifier.compute_distances_two_loops, X_test)
print('Two loop version took %f seconds' % two_loop_time)

one_loop_time = time_function(classifier.compute_distances_one_loop, X_test)
print('One loop version took %f seconds' % one_loop_time)

no_loop_time = time_function(classifier.compute_distances_no_loops, X_test)
print('No loop version took %f seconds' % no_loop_time)


#  3. k-fold cross validation


In [ ]:
num_folds = 5

k_choices = [1, 3, 5, 7, 9, 10, 12, 15, 18, 20, 50, 100]

X_train_folds = []
y_train_folds = []

Split up the training data into folds. After splitting, `X_train_folds` and    
`y_train_folds` should each be lists of length `num_folds`, where                
`y_train_folds[i]` is the label vector for the points in `X_train_folds[i]`.     

In [ ]:
num_train = X_train.shape[0]
fold_size = np.ceil(num_train/num_folds).astype('int')

In the case of `num_train = 5000` and 5 folds, we obtain 
`X_train_folds = np.split(X_train, [1000, 2000, 3000, 4000])`
`y_train_folds = np.split(y_train, [1000, 2000, 3000, 4000])`

In [ ]:
X_train_folds = np.split(X_train, [(i + 1)*fold_size for i in np.arange(num_folds)])
y_train_folds = np.split(y_train, [(i + 1)*fold_size for i in np.arange(num_folds)])


In [ ]:
X_train_folds[1].shape

A dictionary holding the accuracies for different values of $k$ that we find
when running cross-validation. After running cross-validation,
`k_to_accuracies[k]` should be a list of length `num_folds` giving the different
accuracy values that we found when using that value of $k$.

In [ ]:
k_to_accuracies = {}

We perform $k$-fold cross validation to find the best value of $k$. For each     
possible value of $k$, run the $k$-nearest-neighbor algorithm `num_folds` times,   
where in each case you use all but one of the folds as training data and the 
last fold as a validation set. Store the accuracies for all fold and all     
values of k in the `k_to_accuracies` dictionary.  

In [ ]:
for k in k_choices:
  
  k_to_accuracies[k] = []
  classifier = KNearestNeighbor()
  for i in range(num_folds):
      X_cv_training = np.concatenate([x for k, x in enumerate(X_train_folds) if k!=i], axis=0)
      y_cv_training = np.concatenate([x for k, x in enumerate(y_train_folds) if k!=i], axis=0)
      classifier.train(X_cv_training, y_cv_training)
      dists = classifier.compute_distances_no_loops(X_train_folds[i])
      y_test_pred = classifier.predict_labels(dists, k=k)
      k_to_accuracies[k].append(np.mean(y_train_folds[i] == y_test_pred))
  


We print out the computed accuracies.

In [ ]:
for k in sorted(k_to_accuracies):
    for accuracy in k_to_accuracies[k]:
        print('k = %d, accuracy = %f' % (k, accuracy))


We plot the raw observations.

In [ ]:
for k in k_choices:
  accuracies = k_to_accuracies[k]
  plt.scatter([k] * len(accuracies), accuracies)

 We plot the trend line with error bars that correspond to standard deviation.

In [ ]:
accuracies_mean = np.array([np.mean(v) for k,v in sorted(k_to_accuracies.items())])
accuracies_std = np.array([np.std(v) for k,v in sorted(k_to_accuracies.items())])
plt.errorbar(k_choices, accuracies_mean, yerr=accuracies_std)
plt.title('Cross-validation on k')
plt.xlabel('k')
plt.ylabel('Cross-validation accuracy')
plt.show()

 # K-Nearest Neighbor with L1 distance

In [ ]:
class KNearestNeighbor_L1(KNearestNeighbor):
  """ a kNN classifier with L1 distance """

  def __init__(self):
    super().__init__()
    

  def compute_distances_one_loop(self, X):
    """
    We overwrite the compute_distance_one_loop method of the parent class 
    KNearestNeighbor. 
    Compute the distance between each test point in X and each training point
    in self.X_train using one loop and the L1 distance measure.

    Input / Output: Same as compute_distances_two_loops
    """
    num_test = X.shape[0]
    num_train = self.X_train.shape[0]
    dists = np.zeros((num_test, num_train))
    X = X.astype('float')
    for i in range(num_test):
      dists[i, :] = (np.sum(np.abs(self.X_train - X[i,:]), axis = 1))
    return dists 
  
  def compute_distances_two_loops(self, X):
    """
    Compute the distance between each test point in X and each 
    training point in self.X_train using a nested loop over both 
    the training data and the test data.

    Inputs:
    - X: A numpy array of shape (num_test, D) containing test data.

    Returns:
    - dists: A numpy array of shape (num_test, num_train) where 
      dists[i, j] is the L1 distance between the ith test 
      point and the jth training point.
    """
    num_test = X.shape[0]
    num_train = self.X_train.shape[0]
    dists = np.zeros((num_test, num_train))
    X = X.astype('float')
    for i in range(num_test):
      for j in range(num_train):
          dists[i, j] = np.sum(np.abs(self.X_train[j,:] - X[i,:]))
        
        
     
    return dists
       

We create an instance nn form the class `KNearestNeighbor_L1`

In [ ]:
classifier = KNearestNeighbor_L1()

Call the method train of the `KNearestNeighbor` class

In [ ]:
classifier.train(X_train, y_train)

We test our implementation with one loop.

In [ ]:
dists = classifier.compute_distances_one_loop(X_test)
dists.shape  

 Let us now predict labels and run the code below: We use $k = 10$

In [ ]:
y_test_pred = classifier.predict_labels(dists, k=10)

We compute and print the fraction of correctly predicted examples.

In [ ]:
num_correct = np.sum(y_test_pred == y_test)
accuracy = float(num_correct) / len(y_test_pred)
print('Got %d / %d correct => accuracy: %f' % (num_correct, num_test, accuracy)) 

The confusion matrix looks as follows:

In [ ]:
# utility function for plotting confusion matrix
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.metrics import confusion_matrix

def plot_confmat(y_true, y_pred):
    """
    Plot the confusion matrix and save to user_files dir
    """
    conf_matrix = confusion_matrix(y_true, y_pred)
    fig = plt.figure(figsize=(9,9))
    ax = fig.add_subplot(111)
    sns.heatmap(conf_matrix,
                annot=True,
                fmt='.0f')
    plt.title('Confusion matrix')
    ax.set_xticklabels( classes)
    ax.set_yticklabels( classes)
    plt.ylabel('True')
    plt.xlabel('Predicted')
    
plot_confmat(y_test, y_test_pred)    

# k-fold cross validation

In [ ]:
num_folds = 5

k_choices = [1, 3, 5, 7, 9, 10, 12, 15, 18, 20, 50, 100]

X_train_folds = []
y_train_folds = []

We Split up the training data into folds. After splitting, `X_train_folds` and    
`y_train_folds` should each be lists of length `num_folds`, where                
`y_train_folds[i]` is the label vector for the points in `X_train_folds[i]`  

In [ ]:
num_train = X_train.shape[0]
fold_size = np.ceil(num_train/num_folds).astype('int')

 In the case of `num_train = 5000` and 5 folds, we obtain 
`X_train_folds = np.split(X_train, [1000, 2000, 3000, 4000])`
`y_train_folds = np.split(y_train, [1000, 2000, 3000, 4000])`

In [ ]:
X_train_folds = np.split(X_train, [(i + 1)*fold_size for i in np.arange(num_folds)])
y_train_folds = np.split(y_train, [(i + 1)*fold_size for i in np.arange(num_folds)])


A dictionary holding the accuracies for different values of $k$ that we find
when running cross-validation. After running cross-validation,
`k_to_accuracies[k]` should be a list of length num_folds giving the different
accuracy values that we found when using that value of $k$.

In [ ]:
k_to_accuracies = {}

We perform $k$-fold cross validation to find the best value of $k$. For each     
possible value of $k$, run the $k$-nearest-neighbor algorithm `num_folds` times,   
where in each case you use all but one of the folds as training data and the 
last fold as a validation set. Store the accuracies for all fold and all     
values of $k$ in the `k_to_accuracies` dictionary.       

In [ ]:
for k in k_choices:
  
  k_to_accuracies[k] = []
  classifier = KNearestNeighbor_L1()
  for i in range(num_folds):
      X_cv_training = np.concatenate([x for k, x in enumerate(X_train_folds) if k!=i], axis=0)
      y_cv_training = np.concatenate([x for k, x in enumerate(y_train_folds) if k!=i], axis=0)
      classifier.train(X_cv_training, y_cv_training)
      dists = classifier.compute_distances_two_loops(X_train_folds[i])
      y_test_pred = classifier.predict_labels(dists, k=k)
      k_to_accuracies[k].append(np.mean(y_train_folds[i] == y_test_pred))
  


We print out the computed accuracies.

In [ ]:
for k in sorted(k_to_accuracies):
    for accuracy in k_to_accuracies[k]:
        print('k = %d, accuracy = %f' % (k, accuracy))



We plot the raw observations.

In [ ]:
for k in k_choices:
  accuracies = k_to_accuracies[k]
  plt.scatter([k] * len(accuracies), accuracies)

We plot the trend line with error bars that correspond to standard deviation.

In [ ]:
accuracies_mean = np.array([np.mean(v) for k,v in sorted(k_to_accuracies.items())])
accuracies_std = np.array([np.std(v) for k,v in sorted(k_to_accuracies.items())])
plt.errorbar(k_choices, accuracies_mean, yerr=accuracies_std)
plt.title('Cross-validation on k')
plt.xlabel('k')
plt.ylabel('Cross-validation accuracy')
plt.show()